### Imports

In [ ]:
import data_gen as gen
from statistics import mean
from typing import List
from math import sqrt, log, pow, inf

In [46]:
budget = 50000
website_list = ["111","112","113","122","123"]
data = gen.generate_data(budget, website_list, 0.01, 0.3, 0.03)
data


{'111': <data_gen.Website at 0x1094a9490>,
 '112': <data_gen.Website at 0x1094a9310>,
 '113': <data_gen.Website at 0x1094a91f0>,
 '122': <data_gen.Website at 0x1094a9040>,
 '123': <data_gen.Website at 0x1094a9430>}

In [47]:
for website in data.keys():
    print(round(data[website].p,3))
    print(round(mean(data[website].realisations),3))
    print('-----')

0.663
0.66
-----
0.579
0.575
-----
0.558
0.56
-----
0.596
0.596
-----
0.633
0.631
-----


### Algorithms

#### Helper functions

In [30]:
def calc_beta(arm, a):
    return sqrt(a/arm.num)

In [33]:
def get_max_key(input_dict,keys):
    new_dict = dict()
    for item in keys:
        new_dict[item] = input_dict[item]
    return max(new_dict, key=new_dict.get)


def get_min_key(input_dict, keys):
    new_dict = dict()
    for item in keys:
        new_dict[item] = input_dict[item]
    return min(new_dict, key=new_dict.get)


In [95]:
def select_arm(current_arms, m, a):   
    current_arms = [data[arm_name] for arm_name in data.keys()]

    ukt_dict = dict()
    lkt_dict = dict()
    bkt_dict = dict()
    beta_dict = dict()
    # Compute Uk(t) and Lk(t) for each arm",
    for k in current_arms:
        beta_dict[k] = calc_beta(k, a)
        ukt = k.last_average + beta_dict[k]
        lkt = k.last_average - beta_dict[k]
        ukt_dict[k] = ukt
        lkt_dict[k] = lkt
    # Compute Bk(t) for each arm",
    for k in current_arms:
        ukt_dict_subset = ukt_dict.copy()
        ukt_dict_subset.pop(k)
        # Find max Ukt
        ukt_subset_sorted = dict(
            sorted(ukt_dict_subset.items(), key=lambda item: item[1]))
        max_ukt = list(ukt_subset_sorted.keys())[-m]
        bkt = ukt_dict[max_ukt] - lkt_dict[k]
        bkt_dict[k] = bkt

    # Identify the set of m arms J(t)\n",
    bkt_dict_sorted = dict(sorted(bkt_dict.items(), key=lambda item: item[1]))
    Jt = set(list(bkt_dict_sorted.keys())[:m])

    # Identify arm with minimum lower bound in J(t)\n",
    lowest = inf
    contenders = []
    for arm in Jt:
        if lkt_dict[arm] <= lowest:
            contenders.append(arm)
    if len(contenders) > 1:
        lower = get_min_key(beta_dict, contenders)
    else:
        lower = contenders[0]
    # Identify arm with maximum upper bound *not* in J(t)\n",
    not_in_jt = list(set(ukt_dict.keys()) - Jt)
    highest = -inf
    contenders = []
    for arm in not_in_jt:
        if ukt_dict[arm] >= highest:
            contenders.append(arm)
    if len(contenders) > 1:
        upper = get_max_key(beta_dict, contenders)
    else:
        upper = contenders[0]
    # Identify and pull arm I(t)
    keyz = [lower, upper]
    It = get_max_key(beta_dict, keyz)
    It.pull()

    return Jt, bkt_dict


#### UGabEB

###### UGabE Budget implementation

In [ ]:
def UGapEb(data, m, budget, a):
    K = len(data)
    ## Initialise
    for arm_name in data.keys():
        data[arm_name].pull()
    ## Main loop
    Jt = ''
    bkt_dict = ''
    t = 0
    for t in range(K+1,budget):
        current_arms = [data[arm_name] for arm_name in data.keys()]
        Jt, bkt_dict = select_arm(current_arms, m, a)

    return Jt


budget = 50000
website_list = ["111", "112", "113", "122", "123"]
data = gen.generate_data(budget, website_list, 0.01, 0.3, 0.03)
best = UGapEb(data, 3, 10000, 100)

for website in data.keys():
    print(f'{data[website].name}: p={round(data[website].p, 3)}')
print()
for website in best:
    print(
        f'website: {website.name}, num: {website.num}, average: {website.average}, true: {website.p}')



In [4]:
budget = 50000
website_list = ["111", "112", "113", "122", "123"]
data = gen.generate_data(budget, website_list, 0.1, 0.3, 0.01)
arms = [data[arm_name] for arm_name in data.keys()]
print(sum(arms[0].realisations))
print(sum(arms[1].realisations))
print(sum(arms[2].realisations))
print(sum(arms[3].realisations))
print(sum(arms[4].realisations))


31784
34276
32390
33787
32568


#### UGapEc

In [113]:
def UGapEc(data, e, m, delta, c):
    K = len(data)
    
    ## Initialise
    for arm_name in data.keys():
        data[arm_name].pull()

    ## Main loop
    Jt = ''
    Bkt_dict = ''
    reason = ''
    t = K + 1

    stopping_criteria = True
    while (stopping_criteria):
        current_arms = [data[arm_name] for arm_name in data.keys()]

        a = c * log((4*K*(t**3))/delta)
        print(a)
        Jt, Bkt_dict = select_arm(current_arms, m, a)

        key = get_max_key(Bkt_dict, Jt)
        t += 1
        if (Bkt_dict[key] >= e):
            stopping_criteria = False
    return Jt

In [116]:
optimal_arms = UGapEc(data, 0.95, 3, 10000, 0.5)
for website in optimal_arms:
    print(
        f'website: {website.name}, num: {website.num}, average: {website.average}, true: {website.p}')

0.7316277011280095
0.962853720868897
1.1631508098056809
1.3398253632902561
1.4978661367769954
1.6408314064834828
1.7713484719679276
1.8914125334782321
2.002574491708815
2.106063798939242
2.2028715806455987
2.293808513370251
2.379546134130174
2.4606469660355876
2.5375869076169133
2.6107721538710615
2.680552177323401
2.7472298211796513
2.8110692428078456
2.8723022345882283
2.9311333043181502
2.9877437962924205
3.0422952625487327
3.094932242265638
3.14578456977916
3.194969304013646
3.242592351485517
3.2887498394856474
3.333529284210169
3.3770105895200473
3.419266904970092
3.4603653662522635
3.5003677368755057
3.5393309664803967
3.5773076784568314
3.6143465973423887
3.6504929247109796
3.6857886708262706
3.7202729481633185
3.7539822319414067
3.7869505920195694
3.819209899851015
3.8507900136477633
3.8817189444518667
3.912023005428146
3.9417269463724156
3.970854075158068
3.9994263676141095
4.027464567132339
4.054988275134633
4.082016033388651
4.108565399037753
4.134653013105556
4.160294663144

IndexError: list index out of range

In [ ]:
delta = 0.9
c = 0.5
optimal_arms = UGapEb(data, 0.6, 3, delta, c)
for arm in optimal_arms:
    print(arm.name)

#### Unified UGapE

In [108]:
def UGapE(data, accuracy, budget, confidence, m, c):
    K = len(data)

    ## Initialise
    for arm_name in data.keys():
        data[arm_name].pull()

    ## Main loop
    Jt = ''
    Bkt_dict = ''
    reason = ''
    t = K + 1
    stopping_criteria = True
    while (stopping_criteria):
        budget -= t
        current_arms = [data[arm_name] for arm_name in data.keys()]
        a = c * log((4*K*(t**3))/confidence)
        print(a)
        print("hallo")
        Jt, Bkt_dict = select_arm(current_arms, m, a)

        key = get_max_key(Bkt_dict, Jt)
        t += 1
        if (Bkt_dict[key] >= accuracy):
            stopping_criteria = False
            reason = 'Terminated because specified accuracy has been satisfied'
        elif budget == 0:
            stopping_criteria = False
            reason = 'Terminatd because budget is exhausted'
    return Jt, reason, Bkt_dict[key]
    


#### Testing

In [110]:
budget = 50000
website_list = ["111", "112", "113", "122", "123"]
data = gen.generate_data(budget, website_list, 0.01, 0.3, 0.03)
print("Generated data: ")
for website in data.keys():
    print(f'{data[website].name}: p={round(data[website].p, 3)}')

print("Results: ")
optimal_arms, reason, hoer = UGapE(data, 0.95, budget=10000, confidence=100, m=3, c=0.5)
print(hoer)
print(reason)
print(hoer)
for website in optimal_arms:
    print(
        f'website: {website.name}, num: {website.num}, average: {website.average}, true: {website.p}')


Generated data: 
111: p=0.616
112: p=0.635
113: p=0.668
122: p=0.591
123: p=0.638
Results: 
1.8829202476250324
hallo
2.744390823206514
Terminated because specified accuracy has been satisfied
2.744390823206514
website: 112, num: 2, average: 0.5, true: 0.6345568398595277
website: 113, num: 1, average: 0.0, true: 0.6675125046142872
website: 111, num: 1, average: 1.0, true: 0.6163592794880726
